In [1]:
import magmaforge
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt


import warnings
warnings.filterwarnings("ignore", category=DeprecationWarning)

In [2]:


def plot_phase_fractions(phase_frac_tbl, ax=None):
    mineral_frac_tbl = phase_frac_tbl.drop(columns=['Liquid','Water'])
    # mineral_frac_tbl.index = [int(iT-273) for iT in mineral_frac_tbl.index]
    mineral_frac_tbl.index = mineral_frac_tbl.index - 273
    fTOL = 1e-4
    cols = mineral_frac_tbl.max(axis=0)>fTOL

    mineral_frac_tbl.loc[::-1, cols].plot.bar(stacked=True, ax=ax)
    
    if ax is None:
        ax = plt.gca()
        
    ax.set_xlabel('Temp [C]')
    ax.set_ylabel('Mass Fraction')
    
def plot_magma_evolution(history):
    phase_frac_tbl = history.phase_frac_table
    
    liq_comp = history.liquid_comp_table
    liq_comp.index -= 273.15


    fig, ax = plt.subplots(nrows=3, sharex=False, squeeze=True, figsize=(5,10) )

    iax = ax[0]
    plot_phase_fractions(phase_frac_tbl, ax=iax)
    iax.set_xticklabels([])
    iax.set_xlabel('')

    iax=ax[1]
    liq_comp.plot(y=['MgO','FeO','Fe2O3','Al2O3','K2O','Na2O','H2O'], ax=iax).legend(loc='upper left')
    # iax.set_xlabel('Temp [C]')
    iax.set_ylabel('Magma Comp [wt%]')
    iax.set_xticklabels([])


    iax=ax[2]
    liq_comp.plot(y='SiO2', ax=iax, legend=True)
    iax.set_xlabel('Temp [C]')
    iax.set_ylabel('Magma Comp [wt%]')


In [3]:
comp={
    'Thingmuli_MSG': {
        'SiO2':48.3622,
        'TiO2': 2.5243,
        'Al2O3': 12.8218,
        'Fe2O3': 5.3011,
        'FeO':  9.5743,
        'MnO':  0.2304,
        'MgO':  5.2089,
        'CaO':  10.1773,
        'Na2O':  2.9250,
        'K2O':  0.2604,
        'P2O5':  0.3406,
        'H2O':  0.2,},
    'Thingmuli': {
        'SiO2':49.91,
        'TiO2': 1.47,
        'Al2O3': 17.91,
        'Fe2O3': 2.45,
        'FeO':  7.02,
        'MnO':  0.0, #0.16
        'MgO':  6.62,
        'CaO':  10.02,
        'Na2O':  3.02,
        'K2O':  0.64,
        'P2O5':  0.2,
        'H2O':  0.2,},
}
T0 = 1200.00+273+50

In [4]:
sys_low = magmaforge.System(comp=comp['Thingmuli'], P=1e3, T0=T0, 
                            O2_buffer='NNO', del_fO2=-3, frac_remains=.001)
sys_med = magmaforge.System(comp=comp['Thingmuli'], P=1e3, T0=T0, 
                            O2_buffer='NNO', del_fO2=0, frac_remains=.001)
sys_hi  = magmaforge.System(comp=comp['Thingmuli'], P=1e3, T0=T0, 
                            O2_buffer='NNO', del_fO2=+3, frac_remains=.001)

In [6]:
sys_low.crystallize(method='frac', fix_fO2=True, Tstep=5, calc_args={'stats':False, 'debug':1});

Liquid is the omnicomponent phase.
kc Fe3+/Fe2+ input grams Fe2O3, FeO 0.08088385274607017 0.820782217749009
kc Fe3+/Fe2+ comp  grams Fe2O3, FeO 0.0822915757935927 0.8195155330497998
******************************** 
Calculating saturation state for Quartz
Affinity, mole fraction 2161.810589076951 [1.]
 
******************************** 
Calculating saturation state for Orthopyroxene
Affinity, mole fraction 593.7259086575286 [-1.13889185  0.92493862  1.16742245  0.01818546 -0.01728433  0.04356155
  0.0020681 ]
 
******************************** 
Calculating saturation state for Water
Affinity, mole fraction 15421.025599534623 [1.]
 
******************************** 
Calculating saturation state for Olivine
Affinity, mole fraction 255.07707497883666 [0.         0.78581154 0.         0.         0.0135991  0.20058936]
 
Exit constraint matrix and RQ decomposition.

Quadratic solution, SVD algorithm, rank 21
Re-inflated delta n solution vector: (37, 1)
 1.604e-05 -3.590e-06 -5.329e-07 -6.6

SystemError: <class 'numpy.linalg.LinAlgError'> returned a result with an exception set

In [ ]:
sys_med.crystallize(method='frac', fix_fO2=True, Tstep=5, calc_args={'stats':False, 'debug':0});

In [ ]:
sys_hi.crystallize(method='frac', fix_fO2=True, Tstep=5, calc_args={'stats':False, 'debug':0});

In [ ]:
plot_magma_evolution(sys_low.history)

In [ ]:
plot_magma_evolution(sys_med.history)
plt.savefig('figs/magma-evo-nno.png', dpi=450)

In [ ]:
plot_magma_evolution(sys_hi.history)

In [ ]:
def get_magma_evo_table(sys:magmaforge.System) -> pd.DataFrame:
    evo_tbl = sys.history.liquid_comp_table
    evo_tbl['rho'] = sys.history.get_liquid_densities()
    evo_tbl['rho_ref'] = sys.history.get_liquid_ref_densities()
    
    return evo_tbl

magma_evo_low = get_magma_evo_table(sys_low)
magma_evo_med = get_magma_evo_table(sys_med)
magma_evo_hi = get_magma_evo_table(sys_hi)



In [ ]:
def plot_TAS(magma_evo:pd.DataFrame, axs:list[plt.axis], color='', label='', rho_ref0=1):
    ax0 = axs[0]
    ax1 = axs[1]
    ind_SiO2_max = magma_evo['SiO2'].argmax()
    magma_evo = magma_evo.copy()
    
        
    
    magma_evo['TotAlk'] = magma_evo['Na2O'] + magma_evo['K2O']
    
    pre_Qz_evo = magma_evo.iloc[:ind_SiO2_max]
    post_Qz_evo = magma_evo.iloc[ind_SiO2_max:]
    # ax.plot(magma_evo['SiO2'], magma_evo['K2O']+magma_evo['Na2O'], '-', color=color, label=label)
    ax0.plot(pre_Qz_evo['SiO2'], pre_Qz_evo['TotAlk'], '-', color=color, label=label)
    ax0.plot(post_Qz_evo['SiO2'], post_Qz_evo['TotAlk'], ':', color=color)
    

    ax0.set_ylabel('Na$_2$O + K$_2$O  [wt%]')

    
    ax1.plot(pre_Qz_evo['SiO2'], 100*(pre_Qz_evo['rho_ref']/rho_ref0-1), '-', color=color, label=label)
    ax1.plot(post_Qz_evo['SiO2'], 100*(post_Qz_evo['rho_ref']/rho_ref0-1), ':', color=color)
    
    ax1.set_ylabel('Magma Density Change [%]')
    ax1.set_xlabel('SiO$_2$  [wt%]')


rho_ref0 = magma_evo_med.iloc[0]['rho_ref']


plt.figure()
fig, axs = plt.subplots(nrows=2, sharex=True, squeeze=True, figsize=(5,7) )
plot_TAS(magma_evo_hi, axs, color='r', label='NNO+3', rho_ref0=rho_ref0) 
plot_TAS(magma_evo_med, axs, color=[.5,.5,.5], label='NNO', rho_ref0=rho_ref0)
plot_TAS(magma_evo_low, axs, color='b', label='NNO-3', rho_ref0=rho_ref0)
plt.legend()

plt.savefig('figs/redox-sensitive-magma-evo.png', dpi=450)